In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.naive_bayes import MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import LinearSVC
from io import StringIO
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_selection import chi2
import numpy as np
from sklearn.externals import joblib
from sklearn.neural_network import MLPClassifier
from sklearn.svm import SVC, NuSVC
from sklearn.multiclass import OneVsOneClassifier
from sklearn.neighbors import NearestCentroid
from sklearn.linear_model import Perceptron

In [2]:
df = pd.read_csv('train_tweets_full_wpp.csv',names = ["userID","tweets"])
df = df[pd.notnull(df['tweets'])]
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 328932 entries, 0 to 328931
Data columns (total 2 columns):
userID    328932 non-null int64
tweets    328932 non-null object
dtypes: int64(1), object(1)
memory usage: 7.5+ MB


In [3]:
col = ['userID', 'tweets']
df = df[col]
df.columns = ['userID', 'tweets']
df['category_id'] = df['userID'].factorize()[0]
category_id_df = df[['userID', 'category_id']].drop_duplicates().sort_values('category_id')
category_to_id = dict(category_id_df.values)
id_to_category = dict(category_id_df[['category_id', 'userID']].values)
df.head()

userID                                             tweets  category_id
0    8746     @handle Let's try and catch up live next week!            0
1    8746  Going to watch Grey's on the big screen - Thur...            0
2    8746  @handle My pleasure Patrick....hope you are well!            0
3    8746  @handle Hi there! Been traveling a lot and lot...            0
4    8746  RT @handle Looking to Drink Clean & Go Green? ...            0

In [4]:
#TF-IDF Settings
tfidf = TfidfVectorizer(analyzer='word', stop_words='english',sublinear_tf=True, max_df=0.5)

In [11]:
%%time
# X_train = df['tweets']
# y_train = df['userID']
X_train, X_test, y_train, y_test = train_test_split(df['tweets'], df['userID'], test_size=0.1, random_state=2)

# tfidf.fit(df['tweets'])

CPU times: user 104 ms, sys: 269 ms, total: 373 ms
Wall time: 702 ms


In [13]:
%%time
xtrain_tfidf =  tfidf.fit_transform(X_train)
xtest_tfidf = tfidf.fit_transform(X_test)
count_vect = CountVectorizer(analyzer='word', stop_words='english')
X_train_counts = count_vect.fit_transform(X_train)
tfidf_transformer = TfidfTransformer()
x_train_tfidf = tfidf_transformer.fit_transform(xtrain_tfidf)
x_test_tfidf = tfidf_transformer.fit_transform(xtest_tfidf)
X_train_tfidf = tfidf_transformer.fit_transform(X_train_counts)

CPU times: user 12.9 s, sys: 582 ms, total: 13.5 s
Wall time: 13.9 s


In [7]:
%%time
#Liner Model Logistic Regression
clf = LinearSVC().fit(x_train_tfidf, y_train)


CPU times: user 1h 55min 32s, sys: 1min 10s, total: 1h 56min 43s
Wall time: 2h 4min 51s


In [15]:
clf.score(x_test_tfidf,y_test)

ValueError: X has 36428 features per sample; expecting 131696

In [ ]:
%%time
#Nearest Neighbors
clf = NearestCentroid(metric='manhattan')
clf.fit(X_train_tfidf, y_train)

In [ ]:
%%time
#MLP Classifier
clf = MLPClassifier(solver='lbfgs', alpha=1e-5,hidden_layer_sizes=(5, 2), random_state=1)
clf.fit(X_train_tfidf,y_train)

In [ ]:
%%time
#SVM
clf = NuSVC(nu=0.5, kernel='rbf', degree=3, gamma='auto_deprecated', coef0=0.0, shrinking=True, probability=False, tol=0.001, cache_size=200, class_weight=None, verbose=False, max_iter=-1, decision_function_shape='ovr', random_state=None)
clf.fit(X_train, y_train)

In [ ]:
%%time
#Linear Perceptron
clf = Perceptron()
clf.fit(x_train_tfidf, y_train)

In [8]:
print(clf.predict(tfidf.transform(["RT @handle: Director of Global Brand Marketing, Hotels and Casino's $125k + 30% bonus - Orlando Fl http://bit.ly/4kUmBB #jobs #twitjobs"])))


[8746]


In [ ]:
import re
def clean_tweet_text(tweet):
    text = re.sub(r'@\w+\s?', '', tweet)
    text = re.sub(r'http.?://[^\s]+[\s]?', '', text)
    text = re.sub('#\w+\s?', '', text)
    text = text.lower()
    return text

In [9]:
# only link pre processing
import re
def clean_tweet_text(tweet):
    text = re.sub(r'http.?://[^\s]+[\s]?', 'http-web-link', tweet)
    print (text)
    return text

In [10]:
%%time
line_num = 1
with open('./whodunnit/test_tweets_unlabeled.txt') as un_fd:
    with open('result_lin_svc_tfidf_full_wpp.txt','w') as res:
        for line in un_fd.readlines():
            clean_line = clean_tweet_text(line)
            userID = clf.predict(tfidf.transform([clean_line])).tolist()
            print (userID)
            res.write("%s\t%s\n"%(line_num,userID[0]))
            line_num += 1

Some people say that rappers don’t have feelings. We have feelings. Some people say that we are not rappers. That hurts our feelings.

[3477]
Do you know how to tweet on a Blackberry 8830? Send suggestions to twitter@handle.com thanks

[8119]
"Yoga is the cessation of mind." -Patanjali

[6492]
@handle Well, with my millions of dollars, a few bucks here or there rarely makes a difference. ;-)

[8894]
Cambria hotels free guide http-web-linkcheap discount hotels ratings - save money 51

[8297]
May the force of Jesus be with you http-web-link
[1624]
YEAH! It's finally Monday!

[9222]
Martin Laird won in Las Vegas last week with a Corza RS putter (available in Japan), length/46.25", loft/3 degress, lie/71 degrees.

[8363]
Joe's Crab Shack Fundraiser benefitting the Sac AIDS Walk [ TOMORROW ] http-web-link
[476]
i hate my self-portrait painting, I don't know what to do with it

[9390]
FREE system to generate leads! http-web-link
[7552]
Life is tough. But Jesus softens it. Work with us to pro

[8670]
Chicago Bulls&#39; Tyrus Thomas breaks left forearm: Chicago Tribune By KC Johnson Tribune reporter Back on Sep.. http-web-link
[8654]
Our blog, http-web-linkdiscusses web issues, standards, and design tips, and code snipits

[4027]
happy birthday @handle!

[5181]
Im drinking out of a cup that was made in Canada. I didnt know cups were made outside of China.

[3804]
Trade schools see enrollment increases : CLEVELAND -- Andy Lipkin is learning about diesel technology as a seco.. http-web-link
[256]
RT @handle: Attn humans: cereal companies *do not* have your children's best interest at heart.

[1698]
RT @handle male multiple orgasms #sextips http-web-link
[9344]
to lie sometimes on the grass under the trees on a summer's day, listening to the murmur of water is by no means a waste of time.

[177]
RT @handle: SEO for Flash: 5 Tips and Best Practices http-web-link#SEO

[4149]
Break time!!!!

[6511]
Tiger Woods Incredible Putt 2008 http-web-link
[8595]
RT @handle 10 useful Wordpress

[250]
RT @handle Don’t look now, but this is what women think about you: http-web-linkhttp-web-link
[8591]
If yall watched the least you can do is say thanks ! we hadd over 300 people watching, cmon now.

[8381]
Hilarious... http-web-link
[3854]
I'd rather laugh with the sinners than cry with the saints, sinners are much more fun. ~Billy Joel #quote #music #lyrics

[5166]
Only a week away from the Board of Advisors Luncheon with Coach Beamer from Va Tech!

[985]
Just had Thanksgiving Diner. Awesome

[3767]
Oh Up In The Air...you look so good!!

[1808]
Been playing Rock Band The Beatles - backgrounds r 2 cool to focus on the notes. A must have for RB fanatics like me #fauxrock

[3342]
Agrhrhr! The Herald gals are coming in just over an hour and I forgot about the pink lemonade and the cupcakes!! Yikes!

[5046]
50 Cent’s Path of Destruction Bears Down on Jay-Z http-web-link
[5108]
"Taste and see the Lord is good, blessed is the man who takes refuge in HIM." Ps34:8

[2954]
having a Mojito

[9851]
In our are the Dallas Cowboys will be playing here shortly... Yeah!!!

[6211]
@handle yeah, definitely nickboirecords@handle.com

[5388]
Can anybody recommend an RSS app for public Facebook pages that, unlike Social RSS, works halfway reliably?

[1524]
If you listen you will learn especially when your wife is screaming

[6164]
What banking's "elite 8" CIOs feel about the state of the economy and tech challenges http-web-link
[3463]
re: outlook 2010-2011 might not see $ go into pure venture as you will going into growth capital -Mayfield fund panelist #churchillclub

[1064]
Final Countdown: 24 Hearts design @handle: http-web-link
[8865]
Kanye West at the VMA's. Here's a guy who was completely and totally out of line.

[1760]
Customer Service - Will Train - SOMT - Phoenix, AZ | http-web-link
[7995]
RT @handle: RT @handle @handle: Video of Lou Dobbs Announcing departure from CNN - http-web-link#cnn #loudobbs

[9030]
@handle anyone who wants to be a can't-hack-it pantywaist who wear

[5857]
The Sixers' immediate plan, I'm told, is more minutes for rookie guard Jrue Holiday

[6882]
Visiting Brighton, England http-web-link
[2983]
FollowFriday: @handle @handle @handle @handle @handle @handle @handle @handle @handle @handle

[4398]
"There is no failure except in no longer trying." Elbert Hubbard http-web-link
[861]
Domestic Worker Safety & Dignity Project -La Colectiva Website to accompany #socialmedia campaign http-web-link
[3828]
@handle iiiiight. Whteva u say meanie

[9516]
@handle it may take a bit... what would you like and where are you?

[5526]
Sheffield Docs: How the Beatles Rock Kremlin, Disco and Atomic War http-web-link
[1895]
Ridiculous Facebook Status of the Day... http-web-link
[7936]
Off to school. Would anyone like to make me laugh until my sides hurt? It would be greatly appreciated. :)

[4412]
DiRT 2 Giveaway. Win the rally racer for 360 OR PS3! Instructions at HonestGamers: http-web-link#gaming #freestuff

[6110]
"Too much of a good thing can be wond

...

[5857]
@handle Awesome! Do you have a posted copy somewhere? (P.S. Thanks for the RT)

[888]
Off to the Candian Health Food Association Convention in Toronto for the weekend! Time to see all the new health food store products!

[2283]
I was watching a TV Game show and the question was asked, "What is a Mangosteen" I found the answer http-web-link
[5904]
@handle Agreed. GO MICHIGAN.

[6700]
Off to check out the new fast eddies with the husband :)

[7834]
When you get tired of stalking Congress, you can stalk POTUS! http-web-link(a project of @handle)

[6514]
#SocialMedia: Obama Calls Kanye a Jackass: There’s Video Too http-web-link
[3856]
Yankees report: Roster: --RHP Joba Chamberlain again gave the Yankees reason to worry about him in the postseaso.. http-web-link
[7348]
Mornings Suck But Sunday Mornings Suck More! Urgh Sleepy =(

[5003]
Them Crooked Vultures=Zeppelin Fighters of the Stone Age Dave Grohl drums, Josh Homme guitar, John Paul Jones bass http-web-link
[4612]
@handle My day

[4822]
#threewordsaftersex five whole minutes!

[8779]
DJ's pretty good... http-web-link
[7514]
That's @handle! RT : As in, I THINK I'm writing one. Totally not what I am supposed to be working on!

[3230]
@handle So envious that you guys get Common...not that there's anything wrong with Robin Thicke. I'm just saying...I really like Common.

[2987]
@handle dude, that's just wrong :-)

[872]
My new site highlights my professional speaking experience. http-web-link
[6871]
Safety Training Transportation Department, lawmakers push bus safety rules http-web-link
[6636]
@handle DANG u were in SC 2nite....i hate i missed it! :-(

[6156]
#followfriday @handle @handle @handle @handle @handle @handle @handle @handle @handle

[4398]
Come to "Tap Tap Revenge Road Trip Tournament - Zurich!" Tuesday, November 24 from 4:00 pm to 7:00 pm. RSVP NOW to... http-web-link
[6986]
@handle no, their out on a walk(: their taking it to the next level (no leash) lmfao! X))

[2147]
My job is having a book fair wh

[2450]
Good points: When is too much transparency actually a bad thing? techPresident http-web-link
[2706]
KC's Riverstop at Cape Coral Yacht Club loses battle to keep contract with the city. http-web-link
[159]
nice I can hear the concert from my apartment!

[5752]
Mangini: "All of this is based on one end goal – to win first and foremost, but also to improve every day."

[4304]
@handle that sounds incredibly gay LOL

[1910]
@handle Egeorge@handlemedia.com

[8523]
@handle Call me when you get a chance please.

[8145]
AH! You're killing me! Can you please deliver downtown?! RT @handle: http-web-link- Call ahead for take out!

[9484]
Become An Authorized Hitachi Projector Dealer Today! Want To Compete With Pricing & Get Access to Great Products? .. http-web-link
[6551]
@handle There's even deleted scenes!!!!

[7907]
RT @handle CTA board OKs budget; service cuts: http-web-link<< Drag your own stroller on the tracks, says CTA #ctafail

[2967]
If you don't like something, change it. If you

[4667]
Soo in agreement with my blogging cohort @handle! Tweeps looking to get ur music heard follow my girl @handle

[7025]
Walmart Makes New Run at Amazon, but Tackles Best Buy and Supermarkets, too - @handle http-web-link
[9811]
@handle How is it?

[8931]
My cat has been hiding under the bed for the past week to escape the heat. Would I feel the same effect if I slept in a bunk bed?

[528]
Just finished watching Broke: The Movie. http-web-linkHighly, highly recommended. Stay with it until the end to get the point.

[5214]
@handle if you start tweet with @ sign very few people see it. I have a blog post on this if you want to know why. Under Twitter insights

[6596]
And it's Live Like a Suicide. Like.. original. That's.... worth $300+

[3018]
Emmy Awards flip flopping. http-web-linkTrying to find ways to improve their slipping Energized Differentiation & Relevance.

[6867]
Here's a free guide for getting more for your time and bucks online http-web-link
[891]
http-web-linkyeah, that 

[7943]
@handle I'm the fat ass that is more excited for thanksgiving than damn christmas lol

[2845]
Is on his fone

[5783]
can't feel the right side of his face....

[5619]
RT @handle: 250+ Free Photoshop Spray Brushes http-web-link
[9814]
Fall 2009 Beauty:: Plum Lips http-web-link
[61]
Fuchs: 'participatory democracy'=really communism (!) & so we need a communist Internet in a communist society #ipf09

[485]
VIVA - Look Younger, Feel Younger! World's Most Power Antioxidant Health Drink. Business Exploding Join or Order Today! http-web-link
[127]
Much of your pain is self-chosen. ~Kahlil Gibran, The Prophet, 1923

[324]
@handle heyheyhey http-web-link
[3025]
@handle How does a painter loose parts? Too many fumes maybe?

[8345]
cream of wheat <3

[1584]
Anyone working on films in Tucson?

[3897]
106 & Park would be so much better 2day if 50 cent would just take off his shirt

[1177]
@handle wuddup!

[8931]
It's been a very country night at the Utah, so I busted out "Broken Record", to 

In [ ]:
print ((xtrain_tfidf))

In [ ]:
print(clf)